# Eurovision Data Visualization Project

In [2]:
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import altair as alt

## Import data


In [78]:
contestants_df = pd.read_csv('./Data/contestants.csv')
contestants_df.head()

year to_country_id   to_country               performer  \
0  1956            ch  Switzerland               Lys Assia   
1  1956            nl  Netherlands             Jetty Paerl   
2  1956            be      Belgium             Fud Leclerc   
3  1956            de      Germany  Walter Andreas Schwarz   
4  1956            fr       France            Mathé Altéry   

                              song  place_contest  sf_num  running_final  \
0                          Refrain            2.0     NaN            2.0   
1            De Vogels Van Holland            2.0     NaN            1.0   
2  Messieurs Les Noyés De La Seine            2.0     NaN            3.0   
3    Im Wartesaal Zum Großen Glück            2.0     NaN            4.0   
4                   Le Temps Perdu            2.0     NaN            5.0   

   running_sf  place_final  ...  place_sf  points_sf  points_tele_final  \
0         NaN          2.0  ...       NaN        NaN                NaN   
1         NaN          2.0  ...       NaN        NaN                NaN   
2         NaN          2.0  ...       NaN        NaN                NaN   
3         NaN          2.0  ...       NaN        NaN                NaN   
4         NaN          2.0  ...       NaN        NaN                NaN   

   points_jury_final  points_tele_sf  points_jury_sf               composers  \
0                NaN             NaN             NaN        Georg Benz Stahl   
1                NaN             NaN             NaN             Cor Lemaire   
2                NaN             NaN             NaN  Jacques Say;Jean Miret   
3                NaN             NaN             NaN  Walter Andreas Schwarz   
4                NaN             NaN             NaN             André Lodge   

             lyricists                                             lyrics  \
0                  NaN  (Refrain d'amour...)\n\nRefrain, couleur du ci...   
1  Annie M. G. Schmidt  De vogels van Holland zijn zo muzikaal\nZe ler...   
2        Robert Montal  Messieurs les noyés de la Seine\nOuvrez-moi le...   
3                  NaN  Es gibt einen Hafen, da fährt kaum ein Schiff\...   
4      Rachèle Thoreau  Chante, carillon\nLe chant du temps perdu\nCha...   

                               youtube_url  
0  https://youtube.com/watch?v=IyqIPvOkiRk  
1  https://youtube.com/watch?v=u45UQVGRVPA  
2  https://youtube.com/watch?v=U9O3sqlyra0  
3  https://youtube.com/watch?v=BDNARIDnmTc  
4  https://youtube.com/watch?v=dm1L0XyikKI  

[5 rows x 21 columns]

In [4]:
contestants_df.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1734 entries, 0 to 1733
Data columns (total 21 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   year               1734 non-null   int64  
 1   to_country_id      1734 non-null   object 
 2   to_country         1734 non-null   object 
 3   performer          1734 non-null   object 
 4   song               1731 non-null   object 
 5   place_contest      1678 non-null   float64
 6   sf_num             640 non-null    float64
 7   running_final      1398 non-null   float64
 8   running_sf         605 non-null    float64
 9   place_final        1397 non-null   float64
 10  points_final       1385 non-null   float64
 11  place_sf           605 non-null    float64
 12  points_sf          605 non-null    float64
 13  points_tele_final  181 non-null    float64
 14  points_jury_final  181 non-null    float64
 15  points_tele_sf     212 non-null    float64
 16  points_jury_sf     212 n

In [127]:
contestants_df[['to_country_id', 'to_country']].drop_duplicates()

to_country_id   to_country
0               ch  Switzerland
1               nl  Netherlands
2               be      Belgium
3               de      Germany
4               fr       France
...            ...          ...
1507    Azerbaijan   Azerbaijan
1513        Russia       Russia
1568     Australia    Australia
1584       Ukraine      Ukraine
1638            cz      Czechia

[95 rows x 2 columns]

In [125]:
#Data Cleaning
contestants_df.loc[contestants_df['to_country']=='Andorra','to_country_id'] = 'ad'
contestants_df.loc[contestants_df['to_country_id']=='mk','to_country'] = 'North Macedonia'

In [66]:
country_votes_df = pd.read_csv('./Data/votes.csv')
country_votes_df.head()

year  round from_country_id to_country_id from_country to_country  \
0  1957  final              at            nl           at         nl   
1  1957  final              at            fr           at         fr   
2  1957  final              at            dk           at         dk   
3  1957  final              at            lu           at         lu   
4  1957  final              at            de           at         de   

   total_points  tele_points  jury_points  
0             6          NaN          NaN  
1             0          NaN          NaN  
2             0          NaN          NaN  
3             3          NaN          NaN  
4             0          NaN          NaN

In [67]:
country_votes_df.info(memory_usage='deep')

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51354 entries, 0 to 51353
Data columns (total 9 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   year             51354 non-null  int64  
 1   round            51354 non-null  object 
 2   from_country_id  51354 non-null  object 
 3   to_country_id    51354 non-null  object 
 4   from_country     51354 non-null  object 
 5   to_country       51354 non-null  object 
 6   total_points     51354 non-null  int64  
 7   tele_points      11741 non-null  float64
 8   jury_points      11715 non-null  float64
dtypes: float64(2), int64(2), object(5)
memory usage: 16.2 MB


## General stats

### Evolution of the number of participants

Aquí podría ser interesante añadir una línea vertical en el año en que se añadieron las semifinales

In [7]:
## Number of participants per year
participants_year = contestants_df['year'].value_counts()
participants_year = participants_year.to_frame().reset_index()
participants_year.columns = ['year', 'n_participants']
participants_year['year'] = participants_year['year'].astype('int')

In [30]:
alt.Chart(participants_year).mark_line().encode(
    alt.Y('n_participants').title('Number of participants'),
    alt.X('year').title('Years')
).interactive()

alt.Chart(...)

### Evolution of final points awarded

In [29]:
contestants_year_df = contestants_df.pivot_table(index='year', 
                                      values=['points_tele_final', 'points_jury_final', 'points_final'], 
                                      aggfunc='sum').stack().reset_index()

contestants_year_df.columns = ['year', 'source', 'points']

#Plot
alt.Chart(contestants_year_df).mark_line().encode(
    alt.Y('points').title('Total points'),
    alt.X('year').title('Years'),
    color='source:N'
    ).properties(
        width=600,
        height=400
).interactive()

alt.Chart(...)

### Jury vs Televote

Sería interesante colorear por 'Big-Five' vs 'not Big-Five', o si no por categoría país (norte Europa, sur, centro, Asia). También se podría añadir una etiqueta que fuera Winner True or False

In [48]:
votes_df = contestants_df[
    contestants_df['year'] >= 2016][['year', 'to_country', 'points_jury_final', 'points_tele_final']].dropna()
votes_df.columns = ['year', 'country', 'points_jury_final', 'points_tele_final']
votes_df['year'] = votes_df['year'].astype('str')

#Scatter plot
alt.Chart(votes_df).mark_circle(size=60).encode(
    x='points_jury_final',
    y='points_tele_final',
    color='year',
    tooltip=['year', 'country', 'points_jury_final', 'points_tele_final']
).interactive()

alt.Chart(...)

### Puntos y participantes

habría que poner distinta leyenda

In [61]:
contestants_year_df = contestants_df.pivot_table(index='year', 
                                      values=['points_tele_final', 'points_jury_final', 'points_final'], 
                                      aggfunc='sum').reset_index()
year_df = contestants_year_df[['year','points_final']].merge(participants_year, on='year')

base = alt.Chart(year_df).encode(
    alt.X('year').title('Year'),
)

part = base.mark_line(stroke='#57A44C', interpolate='monotone').encode(
    alt.Y('n_participants').title('Number of participants', titleColor='#57A44C'),
    tooltip=['year', 'n_participants']
)

points = base.mark_line(stroke='#5276A7', interpolate='monotone').encode(
    alt.Y('points_final').title('Total Points Final', titleColor='#5276A7'),
    tooltip=['year', 'points_final']
)

alt.layer(part, points).resolve_scale(
    y='independent'
).properties(
    width=600,
    height=400
).configure_legend(
    title=None, orient='right'
)

alt.LayerChart(...)

In [62]:
#Scatter plot
alt.Chart(year_df).mark_circle(size=60).encode(
    x='n_participants',
    y='points_final',
    tooltip=['year', 'points_final', 'points_final']
).interactive()

alt.Chart(...)

### Number of entries in the contest

In [9]:
## Number of entries per country
entries_country = contestants_df.groupby(['to_country'], as_index=False)['to_country'].value_counts()
entries_country.columns = ['country',  'n_entries']
entries_country = entries_country.sort_values(by='n_entries', ascending=False)

In [31]:
alt.Chart(entries_country).mark_bar().encode(
    alt.X("country:N").title("Country").sort('-y'),
    alt.Y('n_entries:Q').title('Number of entries'),
).interactive()

alt.Chart(...)

In [11]:
import geopandas as gpd

url = "./Data/europe.topojson"
gdf_ne = gpd.read_file(url)  # zipped shapefile
gdf_ne = gdf_ne[["NAME", 'geometry']]
gdf_ne.columns = ["country", 'geometry']

alt.Chart(gdf_ne).mark_geoshape()

alt.Chart(...)

In [12]:
# define a pointer selection
click_state = alt.selection_point(fields=["country"])

# create a choropleth map using a lookup transform
# define a condition on the opacity encoding depending on the selection
choropleth = (
    alt.Chart(gdf_ne)
    .mark_geoshape()
    .transform_lookup(
        lookup="country", from_=alt.LookupData(entries_country, "country", ["country", "n_entries"])
    )
    .encode(
        color="n_entries:Q",
        opacity=alt.condition(click_state, alt.value(1), alt.value(0.2)),
        tooltip=["country:N", "n_entries:Q"],
    )
    #.project(type="albersUsa")
)

# create a bar chart with a similar condition on the opacity encoding.
bars = (
    alt.Chart(
        entries_country.nlargest(15, "n_entries"), title="Top 15 countries by entries"
    )
    .mark_bar()
    .encode(
        x="n_entries",
        opacity=alt.condition(click_state, alt.value(1), alt.value(0.2)),
        color="n_entries",
        y=alt.Y("country").sort("-x"),
    )
)

(choropleth & bars).add_params(click_state)

alt.VConcatChart(...)

### Number of wins

Incluir un menú para seleccionar si se quiere ver el nº de veces que ha ganado Eurovisión, Top 3, Top 10, ha pasado a la final

In [13]:
## Number of wins per country
wins_country = contestants_df[contestants_df['place_contest']==1.0].groupby(['to_country'], as_index=False)['to_country'].value_counts()
wins_country.columns = ['country',  'n_wins']

In [14]:
# define a pointer selection
click_state = alt.selection_point(fields=["country"])

# create a choropleth map using a lookup transform
# define a condition on the opacity encoding depending on the selection
choropleth = (
    alt.Chart(gdf_ne)
    .mark_geoshape()
    .transform_lookup(
        lookup="country", from_=alt.LookupData(wins_country, "country", ["country", "n_wins"])
    )
    .encode(
        color="n_wins:Q",
        opacity=alt.condition(click_state, alt.value(1), alt.value(0.2)),
        tooltip=["country:N", "n_wins:Q"],
    )
    #.project(type="albersUsa")
)

# create a bar chart with a similar condition on the opacity encoding.
bars = (
    alt.Chart(
        wins_country.nlargest(11, "n_wins"), title="Top ESC 11 countries"
    )
    .mark_bar()
    .encode(
        x="n_wins",
        opacity=alt.condition(click_state, alt.value(1), alt.value(0.2)),
        color="n_wins",
        y=alt.Y("country").sort("-x"),
    )
)

(choropleth & bars).add_params(click_state)

alt.VConcatChart(...)

-----------
## Geopolitics

Create a graph with the voting pattern trough the years. Include another graph with the most voted countries by a particular country and from which countries does it recieve points.

In [136]:
import networkx as nx
import nx_altair as nxa

In [141]:
country_votes_filter_df = country_votes_df[country_votes_df['round']=='final'][['year', 'from_country', 'to_country', 'total_points']].dropna()
country_votes_filter_df = country_votes_filter_df.groupby(['from_country', 'to_country'], as_index=False)['total_points'].sum()
country_votes_filter_df = country_votes_filter_df.merge(contestants_df[['to_country_id', 'to_country']].drop_duplicates(), how='left',
                                                        left_on='from_country', right_on='to_country_id').drop('to_country_id',axis=1)
country_votes_filter_df.columns = ['from_country', 'to_country', 'total_points', 'from_country_name']
country_votes_filter_df = country_votes_filter_df.merge(contestants_df[['to_country_id', 'to_country']].drop_duplicates(), how='left',
                                                        left_on='to_country', right_on='to_country_id').drop('to_country_id',axis=1)
country_votes_filter_df.columns = ['from_country', 'to_country', 'total_points', 'from_country_name', 'to_country_name']
country_votes_filter_df.dropna(inplace=True)

In [142]:
alt.Chart(country_votes_filter_df).mark_rect().encode(
    x='from_country:N',
    y='to_country:N',
    color='total_points:Q',
    tooltip=['from_country_name', 'to_country_name', 'total_points']
)

alt.Chart(...)

**Nota**: al sacar el grafo habría que normalizar entre el número total de puntos que ha dado un país a lo largo de su historia

In [143]:
#Normalized graph by total number of points given

#Calculate total points a country has given trough its history
country_total_points = country_votes_filter_df.groupby('from_country',as_index=False)['total_points'].sum()
country_total_points.columns = ['from_country', 'overall_points']
country_votes_filter_df = country_votes_filter_df.merge(country_total_points)
country_votes_filter_df['norm_points'] = country_votes_filter_df['total_points'] / country_votes_filter_df['overall_points']

In [144]:
alt.Chart(country_votes_filter_df).mark_rect().encode(
    x='from_country:N',
    y='to_country:N',
    color='norm_points:Q',
    tooltip=['from_country_name', 'to_country_name', 'total_points']
)

alt.Chart(...)

### Friendzone Network

In [149]:
#votes_adj_mx = country_votes_filter_df.pivot_table(values='norm_points', index='from_country', columns='to_country')

In [192]:
country_group_mapping = {'ad': 'Mediterranean',
 'al': 'Balcans',
 'am': 'Middle East-Caucasus',
 'at': 'Western Europe',
 'au': 'Western Europe',
 'az': 'Middle East-Caucasus',
 'ba': 'Balcans',
 'be': 'Western Europe',
 'bg': 'Balcans',
 'by': 'Eastern Europe',
 'ch': 'Western Europe',
 'cs': 'Balcans',
 'cy': 'Balcans',
 'cz': 'Eastern Europe',
 'de': 'Western Europe',
 'dk': 'Northern Europe',
 'ee': 'Eastern Europe',
 'es': 'Mediterranean',
 'fi': 'Northern Europe',
 'fr': 'Western Europe',
 'gb': 'Western Europe',
 'ge': 'Western Europe',
 'gr': 'Balcans',
 'hr': 'Balcans',
 'hu': 'Eastern Europe',
 'ie': 'Western Europe',
 'il': 'Middle East-Caucasus',
 'is': 'Northern Europe',
 'it': 'Mediterranean',
 'lt': 'Eastern Europe',
 'lu': 'Western Europe',
 'lv': 'Eastern Europe',
 'ma': 'Mediterranean',
 'mc': 'Mediterranean',
 'md': 'Eastern Europe',
 'me': 'Balcans',
 'mk': 'Balcans',
 'mt': 'Mediterranean',
 'nl': 'Western Europe',
 'no': 'Northern Europe',
 'pl': 'Eastern Europe',
 'pt': 'Mediterranean',
 'ro': 'Eastern Europe',
 'rs': 'Balcans',
 'ru': 'Eastern Europe',
 'se': 'Northern Europe',
 'si': 'Balcans',
 'sk': 'Eastern Europe',
 'sm': 'Mediterranean',
 'tr': 'Middle East-Caucasus',
 'ua': 'Eastern Europe',
 'yu': 'Balcans'}

In [202]:
th=0.06
votes_graph = nx.from_pandas_edgelist(country_votes_filter_df[country_votes_filter_df['norm_points']>th],
                                       'from_country', 'to_country',
                                       edge_attr=['norm_points','total_points'])

#Create a dictionary mapping each country to its country_id
country_name_mapping = dict(zip(country_votes_filter_df['from_country'], country_votes_filter_df['from_country_name']))
country_id_mapping = dict(zip(country_votes_filter_df['from_country'], country_votes_filter_df['from_country']))

# Add country_id and name as node attributes
nx.set_node_attributes(votes_graph, country_name_mapping, 'country_name')
nx.set_node_attributes(votes_graph, country_id_mapping, 'country_id')
nx.set_node_attributes(votes_graph, country_id_mapping, 'label')
nx.set_node_attributes(votes_graph, country_group_mapping, 'country_group')

# Compute positions for viz.
pos = nx.spring_layout(votes_graph)

#Get edges weights 
weights = list(nx.get_edge_attributes(votes_graph,'norm_points').values())

# Draw the graph using Altair
viz = nxa.draw_networkx(
    votes_graph, pos=pos,
    width='norm_points',
    node_color = 'country_group',
    #edge_color='norm_points', 
    #edge_cmap='greys', 
    #width=[ x*10 for x in weights]
    edge_tooltip=['norm_points', 'total_points'],
    node_tooltip=['country_id', 'country_name']
)


# Show it as an interactive plot!
viz.properties(
    width=600,
    height=400
).interactive()



alt.LayerChart(...)

-------------
## Songs

### Wordcloud

https://medium.com/@thalia181189/want-to-create-fully-interactive-plots-with-python-d54ab28760d9

In [15]:
import pandas as pd
from matplotlib import pyplot as plt
import altair as alt
from altair import *
from ipywidgets import widgets, interact, interactive, fixed, Button, Layout
from wordcloud import WordCloud, STOPWORDS, ImageColorGenerator
from string import digits 
import spacy
import nltk
from nltk.corpus import stopwords
from IPython.display import display

In [16]:
contestants_df['lyrics'].head()

0    (Refrain d'amour...)\n\nRefrain, couleur du ci...
1    De vogels van Holland zijn zo muzikaal\nZe ler...
2    Messieurs les noyés de la Seine\nOuvrez-moi le...
3    Es gibt einen Hafen, da fährt kaum ein Schiff\...
4    Chante, carillon\nLe chant du temps perdu\nCha...
Name: lyrics, dtype: object

In [17]:
# Download NLTK resources
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('words')
nltk.download('wordnet')
nltk.download('omw-1.4')
from nltk.tokenize import word_tokenize

# Define stopwords
#stop_words = set(stopwords.words('english'))

# Define stopwords for multiple languages 
stop_words = set(stopwords.words())
#stop_words = set(stopwords.words('english')) | \
#             set(stopwords.words('spanish')) | \
#             set(stopwords.words('french')) | \
#             set(stopwords.words('german'))

# Function to remove stopwords
def remove_stopwords(text):
    tokens = word_tokenize(text)
    filtered_tokens = [word for word in tokens if word.lower() not in stop_words]
    return ' '.join(filtered_tokens)

# Function to lemmatize text
def lemmatize(text):
    lemmatizer = nltk.stem.WordNetLemmatizer()
    lemmatized_text = [lemmatizer.lemmatize(word) for word in text.split()]
    return ' '.join(lemmatized_text)

# Function to clean sentences
def clean_sent(text):
    return ' '.join([word for word in text.split() if len(word) > 1])

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\anaso\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\anaso\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package words to
[nltk_data]     C:\Users\anaso\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\anaso\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\anaso\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


In [18]:
contestants_prep_df = pd.read_csv('./Data/contestants_preprocessed.csv')

In [19]:
def full_cleaning(year,frame,col):
    newframe=frame.copy()  
    newframe[col] = newframe[col].str.replace('\d+', '',regex=True).str.replace('?', '', regex=True
        ).str.replace('\W', ' ', regex=True).str.replace("\n", '', regex=True
        ).str.replace('\b(n\w+)\b', '', regex=True).str.lower().str.strip()
    if year != 'Overall':
        newframe = newframe[newframe['year']==year]
    newframe = newframe.astype('str')
    text = ' '.join(newframe[col][:])
    cleantext = remove_stopwords(text)
    words = set(nltk.corpus.words.words())
    cleantext=lemmatize(cleantext) 
    cleantext = clean_sent(cleantext)
    return cleantext
# Define a function to save the image
def save_image(image):
    filename = f'wordcloud_{year}.png'
    plt.savefig(f'./Figures/{filename}')
    print(f'Word cloud image saved as {filename}')
    
###funtion for cloud that Im going to call with interact  ######  
def makingclouds(year,frame,col,maximum,atitle):
    cloudtext=full_cleaning(year,frame,col)
    wordcloud = WordCloud(max_font_size=50, max_words=maximum, background_color="white",collocations=False, 
        font_path='calibri.ttf').generate(cloudtext)
    wordcloud.generate_from_frequencies
    plt.style.use("seaborn-white")
    plt.figure()
    #plt.title(atitle, fontsize=30)#,fontweight="bold")
    plt.imshow(wordcloud, interpolation="bilinear")
    plt.axis("off")
    
    # Create a button widget
    button_layout = Layout(display='flex', justify_content='center')
    save_button = Button(description="Save Image", layout=button_layout)
    # Register the function to be called when the button is clicked
    save_button.on_click(save_image)
    
    # Display the button
    #display(save_button)
    plt.show()  # Display the plot

years_ls = list(contestants_prep_df['year'].unique())
years_ls.append('Overall')
interact(makingclouds, year=years_ls, df=fixed(contestants_df), col=fixed('lyrics'),maximum=[20,50,100,150],
         atitle=fixed('Frequent words in ESC lyrics'), frame=fixed(contestants_prep_df[['year','lyrics']]))

interactive(children=(Dropdown(description='year', options=(1956, 1957, 1958, 1959, 1960, 1961, 1962, 1963, 19…

<function __main__.makingclouds(year, frame, col, maximum, atitle)>